## Section 1: Basic Decoding Algorithms

In [1]:
!uv pip install transformers datasets evaluate markdownify

Using Python 3.11.12 environment at: /usr
Resolved 39 packages in 945ms
⠙ Preparing packages... (0/7)
⠙ Preparing packages... (0/7)
evaluate   ------------------------------     0 B/82.04 KiB
⠙ Preparing packages... (0/7)
evaluate   ------------------------------ 16.00 KiB/82.04 KiB
⠙ Preparing packages... (0/7)
evaluate   ------------------------------ 16.00 KiB/82.04 KiB
⠙ Preparing packages... (0/7)
evaluate   ------------------------------ 32.00 KiB/82.04 KiB
⠙ Preparing packages... (0/7)
evaluate   ------------------------------ 48.00 KiB/82.04 KiB
⠙ Preparing packages... (0/7)
evaluate   ------------------------------ 64.00 KiB/82.04 KiB
⠙ Preparing packages... (0/7)
evaluate   ------------------------------ 64.00 KiB/82.04 KiB
dill       ------------------------------ 14.93 KiB/113.53 KiB
⠙ Preparing packages... (0/7)
evaluate   ------------------------------ 64.00 KiB/82.04 KiB
dill       ------------------------------ 14.93 KiB/113.53 KiB
fsspec     ---------------------------

In [2]:
"""set device and random seeds"""

######################################################
#  The following helper functions are given to you.
######################################################

from tqdm.notebook import tqdm
import torch
import torch.nn.functional as F

device = 'cuda' if torch.cuda.is_available() else 'cpu'
print(f'device: {device}')

def set_seed(seed=19260817):
    torch.manual_seed(seed)
    torch.cuda.manual_seed_all(seed)
    torch.backends.cudnn.deterministic = True
    torch.backends.cudnn.benchmark = False

set_seed()



device: cuda


In [3]:
"""load datasets"""

######################################################
#  The following helper code is given to you.
######################################################

from datasets import load_dataset

dataset = load_dataset('Ximing/ROCStories')
train_data, dev_data, test_data = dataset['train'], dataset['validation'], dataset['test']

print(train_data[0])



/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/131 [00:00<?, ?B/s]

train.jsonl:   0%|          | 0.00/6.53M [00:00<?, ?B/s]

validation.jsonl:   0%|          | 0.00/717k [00:00<?, ?B/s]

test.jsonl:   0%|          | 0.00/713k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/16207 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/1817 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/1819 [00:00<?, ? examples/s]

{'story_id': '080198fc-d0e7-42b3-8e63-b2144e59d816', 'prompt': 'On my way to work I stopped to get some coffee.', 'continuation': 'I went through the drive through and placed my order. I paid the cashier and patiently waited for my drink. When she handed me the drink, the lid came off and spilled on me. The coffee hurt and I had to go home and change clothes.', 'constraint_words': ['drive', 'order', 'drink', 'lid', 'coffee', 'hurt', 'home', 'change', 'clothes']}


In [4]:
"""prepare evaluation"""

######################################################
#  The following helper code is given to you.
######################################################

from evaluate import load
from transformers import RobertaForSequenceClassification, RobertaTokenizer

perplexity_scorer = load("perplexity", module_type="metric")
cola_model_name = "textattack/roberta-base-CoLA"
cola_tokenizer = RobertaTokenizer.from_pretrained(cola_model_name)
cola_model = RobertaForSequenceClassification.from_pretrained(cola_model_name).to(device)

def batchify(data, batch_size):
    assert batch_size > 0

    batch = []
    for item in data:
        # Yield next batch
        if len(batch) == batch_size:
            yield batch
            batch = []

        batch.append(item)

    # Yield last un-filled batch
    if len(batch) != 0:
        yield batch



tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/798k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/564 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/501M [00:00<?, ?B/s]

Some weights of the model checkpoint at textattack/roberta-base-CoLA were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [5]:
"""set up evaluation metric"""

######################################################
#  The following helper code is given to you.
######################################################

def compute_perplexity(texts, model='gpt2', batch_size=8):
    score = perplexity_scorer.compute(predictions=texts, add_start_token=True, batch_size=batch_size, model_id=model)
    return score['mean_perplexity']


def compute_fluency(texts, batch_size=8):
  scores = []
  for b_texts in batchify(texts, batch_size):
    inputs = cola_tokenizer(texts, padding=True, truncation=True, return_tensors="pt").to(device)
    with torch.no_grad():
      logits = cola_model(**inputs).logits
      probs = logits.softmax(dim=-1)
      scores.extend(probs[:, 1].tolist())
  return sum(scores) / len(scores)


def compute_diversity(texts):
    unigrams, bigrams, trigrams = [], [], []
    total_words = 0
    for gen in texts:
        o = gen.split(' ')
        total_words += len(o)
        for i in range(len(o)):
            unigrams.append(o[i])
        for i in range(len(o) - 1):
            bigrams.append(o[i] + '_' + o[i + 1])
        for i in range(len(o) - 2):
            trigrams.append(o[i] + '_' + o[i + 1] + '_' + o[i + 2])
    return len(set(unigrams)) / len(unigrams), len(set(bigrams)) / len(bigrams), len(set(trigrams)) / len(trigrams)


def evaluate(generations, experiment):
  generations = [_ for _ in generations if _ != '']
  perplexity = compute_perplexity(generations)
  fluency = compute_fluency(generations)
  diversity = compute_diversity(generations)
  print(experiment)
  print(f'perplexity = {perplexity:.2f}')
  print(f'fluency = {fluency:.2f}')
  print(f'diversity = {diversity[0]:.2f}, {diversity[1]:.2f}, {diversity[2]:.2f}')
  print()

debug_sents = ["This restaurant is awesome", "My dog is cute and I love it.", "Today is sunny."]
evaluate(debug_sents, 'debugging run')



model.safetensors:   0%|          | 0.00/501M [00:00<?, ?B/s]

config.json:   0%|          | 0.00/665 [00:00<?, ?B/s]

Xet Storage is enabled for this repo, but the 'hf_xet' package is not installed. Falling back to regular HTTP download. For better performance, install the package with: `pip install huggingface_hub[hf_xet]` or `pip install hf_xet`


model.safetensors:   0%|          | 0.00/548M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

...

vocab.json:   0%|          | 0.00/1.04M [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

  0%|          | 0/1 [00:00<?, ?it/s]

debugging run
perplexity = 178.64
fluency = 0.98
diversity = 0.87, 1.00, 1.00



In [6]:
"""load model and tokenizer"""

######################################################
#  The following helper code is given to you.
######################################################

from transformers import GPT2LMHeadModel, GPT2Tokenizer

model_name = 'gpt2'
tokenizer = GPT2Tokenizer.from_pretrained(model_name, pad_token="<|endoftext|>")
model = GPT2LMHeadModel.from_pretrained(model_name).to(device)
model.eval()



GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50257, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D(nf=2304, nx=768)
          (c_proj): Conv1D(nf=768, nx=768)
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D(nf=3072, nx=768)
          (c_proj): Conv1D(nf=768, nx=3072)
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=768, out_features=50257, bias=False)
)

In this section, you will implement a few basic decoding algorithms:
1. Greedy decoding
2. Vanilla sampling
3. Temperature sampling
4. Top-k sampling
5. Top-p sampling

We have provided a wrapper function `decode()` that takes care of batching, controlling max length, and handling the EOS token.
You will be asked to implement the core function of each method: *given the pre-softmax logits of the next token, decide what the next token is.*

**The wrapper calls the core function of each decoding algorithm, which you will implement in the subsections below.**

In [7]:
"""decode main wrapper function"""

######################################################
#  The following helper code is given to you.
######################################################

def decode(prompts, max_len, method, **kwargs):
  encodings_dict = tokenizer(prompts, return_tensors="pt", padding=True)
  input_ids = encodings_dict['input_ids'].to(device)
  attention_mask = encodings_dict['attention_mask'].to(device)

  model_kwargs = {'attention_mask': attention_mask, "use_cache": False}
  batch_size, input_seq_len = input_ids.shape

  unfinished_sequences = torch.ones(batch_size, dtype=torch.long, device=device)

  for step in range(max_len):
    model_inputs = model.prepare_inputs_for_generation(input_ids, **model_kwargs)
    cache_position = torch.arange(0, input_ids.shape[1], dtype=torch.long, device=input_ids.device)
    model_kwargs["cache_position"] = cache_position
    with torch.no_grad():
      outputs = model(**model_inputs, return_dict=True, output_attentions=False, output_hidden_states=False)

    if step == 0:
      last_non_masked_idx = torch.sum(attention_mask, dim=1) - 1
      next_token_logits = outputs.logits[range(batch_size), last_non_masked_idx, :]
    else:
      next_token_logits = outputs.logits[:, -1, :]

    log_prob = F.log_softmax(next_token_logits, dim=-1)

    if method == 'greedy':
      next_tokens = greedy(next_token_logits)
    elif method == 'sample':
      next_tokens = sample(next_token_logits)
    elif method == 'temperature':
      next_tokens = temperature(next_token_logits, t=kwargs.get('t', 0.8))
    elif method == 'topk':
      next_tokens = topk(next_token_logits, k=kwargs.get('k', 20))
    elif method == 'topp':
      next_tokens = topp(next_token_logits, p=kwargs.get('p', 0.7))

    # finished sentences should have their next token be a padding token
    next_tokens = next_tokens * unfinished_sequences + tokenizer.pad_token_id * (1 - unfinished_sequences)

    input_ids = torch.cat([input_ids, next_tokens[:, None]], dim=-1)
    model_kwargs = model._update_model_kwargs_for_generation(outputs, model_kwargs, is_encoder_decoder=model.config.is_encoder_decoder)

    # if eos_token was found in one sentence, set sentence to finished
    unfinished_sequences = unfinished_sequences.mul((next_tokens != tokenizer.eos_token_id).long())

    if unfinished_sequences.max() == 0:
      break

  response_ids = input_ids[:, input_seq_len:]
  response_text = [tokenizer.decode(output, skip_special_tokens=True, clean_up_tokenization_spaces=True) for output in response_ids]

  return response_text



In [8]:
"""debug helper code"""

######################################################
#  The following helper code is given to you.
######################################################

# For debugging, we duplicate a single prompt 10 times so that we obtain 10 generations for the same prompt
dev_prompts = [dev_data[0]['prompt']] * 10

def print_generations(prompts, generations):
  for prompt, generation in zip(prompts, generations):
    print(f'{[prompt]} ==> {[generation]}')



### 1.1 Greedy Decoding

In [9]:
def greedy(next_token_logits):
  '''
  inputs:
  - next_token_logits: Tensor(size = (B, V), dtype = float)
  outputs:
  - next_tokens: Tensor(size = (B), dtype = long)
  '''

  # TODO: compute `next_tokens` from `next_token_logits`.
  # Hint: use torch.argmax()
  next_tokens = torch.argmax(next_token_logits, dim=-1)

  return next_tokens


generations = decode(dev_prompts, max_len=20, method='greedy')
print_generations(dev_prompts, generations)

['Ryan was called by his friend to skip work one day.'] ==> ['\n\n"I was like, \'I\'m going to go to work tomorrow,\'" he said.']
['Ryan was called by his friend to skip work one day.'] ==> ['\n\n"I was like, \'I\'m going to go to work tomorrow,\'" he said.']
['Ryan was called by his friend to skip work one day.'] ==> ['\n\n"I was like, \'I\'m going to go to work tomorrow,\'" he said.']
['Ryan was called by his friend to skip work one day.'] ==> ['\n\n"I was like, \'I\'m going to go to work tomorrow,\'" he said.']
['Ryan was called by his friend to skip work one day.'] ==> ['\n\n"I was like, \'I\'m going to go to work tomorrow,\'" he said.']
['Ryan was called by his friend to skip work one day.'] ==> ['\n\n"I was like, \'I\'m going to go to work tomorrow,\'" he said.']
['Ryan was called by his friend to skip work one day.'] ==> ['\n\n"I was like, \'I\'m going to go to work tomorrow,\'" he said.']
['Ryan was called by his friend to skip work one day.'] ==> ['\n\n"I was like, \'I\'m goin

### 1.2 Vanilla Sampling and Temperature Sampling

In [10]:
def sample(next_token_logits):
  '''
  inputs:
  - next_token_logits: Tensor(size = (B, V), dtype = float)
  outputs:
  - next_tokens: Tensor(size = (B), dtype = long)
  '''

  # TODO: compute the probabilities `probs` from the logits.
  # Hint: `probs` should have size (B, V)
  probs = F.softmax(next_token_logits, dim=-1)

  # TODO: compute `next_tokens` from `probs`.
  # Hint: use torch.multinomial()
  next_tokens = torch.multinomial(probs, num_samples=1).squeeze(-1)

  return next_tokens


set_seed()
generations = decode(dev_prompts, max_len=20, method='sample')
print_generations(dev_prompts, generations)

['Ryan was called by his friend to skip work one day.'] ==> ['\n\nKiddiak said he stepped on it, hit the brakes hard and decided to cross first']
['Ryan was called by his friend to skip work one day.'] ==> [" Their interaction didn't work at all by the time he would get back to Louisville. Some details that"]
['Ryan was called by his friend to skip work one day.'] ==> [' According to investigators at the time, Gianfranco was yelling at them for not doing enough work']
['Ryan was called by his friend to skip work one day.'] ==> [' "No, my boyfriend doesn\'t do work," Cat started, desperate to dial a phone in distress']
['Ryan was called by his friend to skip work one day.'] ==> [' Later, he did not show up for school again until late the next day. After catching a train']
['Ryan was called by his friend to skip work one day.'] ==> [' The fliers denounced Gov. Pat Brown for having insufficient police presence in the building, and he engineered']
['Ryan was called by his friend to skip wo

In [11]:
def temperature(next_token_logits, t):
  '''
  inputs:
  - next_token_logits: Tensor(size = (B, V), dtype = float)
  - t: float
  outputs:
  - next_tokens: Tensor(size = (B), dtype = long)
  '''

  # TODO: compute the probabilities `probs` from the logits, with temperature applied.
  probs = F.softmax((next_token_logits/t), dim=-1)

  # TODO: compute `next_tokens` from `probs`.
  next_tokens = torch.multinomial(probs, num_samples=1).squeeze(-1)

  return next_tokens


set_seed()
generations = decode(dev_prompts, max_len=20, method='temperature', t=0.8)
print_generations(dev_prompts, generations)

['Ryan was called by his friend to skip work one day.'] ==> ['\n\nKiddiak said he stepped on the blood spur out of pity from his cousin Jimmie']
['Ryan was called by his friend to skip work one day.'] ==> [" Their interaction didn't go well.\n\nHerad's mother was in a panic. Unable to"]
['Ryan was called by his friend to skip work one day.'] ==> [" He said he hadn't asked if he'd be coming back to work for a week.\n\n"]
['Ryan was called by his friend to skip work one day.'] ==> [' "I told my boss I was leaving work early to take care of my sons\' homework. So']
['Ryan was called by his friend to skip work one day.'] ==> [' He also said he was going to play out of town because the game was cancelled. Johnson also said']
['Ryan was called by his friend to skip work one day.'] ==> [' The next morning, after talking to other parents who also work in the area, he was told to']
['Ryan was called by his friend to skip work one day.'] ==> [' It was before he was going to college.\n\n"Oh, I\'l

### 1.3 Top-k Sampling

In [12]:
def topk(next_token_logits, k):
  '''
  inputs:
  - next_token_logits: Tensor(size = (B, V), dtype = float)
  - k: int
  outputs:
  - next_tokens: Tensor(size = (B), dtype = long)
  '''

  # TODO: Keep only top-k tokens with highest probabilities.
  # Hint: use torch.topk()
  topk_logits, topk_indices = torch.topk(next_token_logits, k=k, dim=-1)

  # Create a mask to zero out all logits not in top-k
  indices_to_remove = next_token_logits < topk_logits[:, -1].unsqueeze(1)

  # Mask the logits
  next_token_logits[indices_to_remove] = float('-inf')

  # TODO: Sample from the masked logits
  probs = F.softmax(next_token_logits, dim=1)
  next_tokens = torch.multinomial(probs, num_samples=1).squeeze(-1)

  return next_tokens


set_seed()
generations = decode(dev_prompts, max_len=20, method='topk', k=20)
print_generations(dev_prompts, generations)

['Ryan was called by his friend to skip work one day.'] ==> ['\n\n"I wasn\'t sure what to expect, so he asked me why I didn\'t work']
['Ryan was called by his friend to skip work one day.'] ==> ['\n\n"I\'m tired of talking about this because it\'s a big distraction. I\'m tired']
['Ryan was called by his friend to skip work one day.'] ==> [' When he arrived at work, the other workers were on the line and asked if he would be willing']
['Ryan was called by his friend to skip work one day.'] ==> [' "Why don\'t you try to do work? You don\'t look like a person," his friend']
['Ryan was called by his friend to skip work one day.'] ==> [' He said he did not have enough money to pay his bills. He told his girlfriend, a teacher']
['Ryan was called by his friend to skip work one day.'] ==> [' The next morning, after work, he would get back to his job, and the next day,']
['Ryan was called by his friend to skip work one day.'] ==> [" It was the first time they had ever met, and they couldn't qui

### 1.4 Top-p Sampling

In [13]:
def topp(next_token_logits, p):
  '''
  inputs:
  - next_token_logits: Tensor(size = (B, V), dtype = float)
  - p: float
  outputs:
  - next_tokens: Tensor(size = (B), dtype = long)
  '''

  # TODO: Sort the logits in descending order, and compute
  # the cumulative probabilities `cum_probs` on the sorted logits
  sorted_logits, sorted_indices = torch.sort(next_token_logits, descending=True, dim=-1)
  sorted_probs = F.softmax(sorted_logits, dim=-1)
  cum_probs = torch.cumsum(sorted_probs, dim=-1)

  # Create a mask to zero out all logits not in top-p
  sorted_indices_to_remove = cum_probs > p
  sorted_indices_to_remove[:, 1:] = sorted_indices_to_remove[:, :-1].clone()
  sorted_indices_to_remove[:, 0] = 0
  # Restore mask to original indices
  indices_to_remove = sorted_indices_to_remove.scatter(dim=1, index=sorted_indices, src=sorted_indices_to_remove)

  # Mask the logits
  next_token_logits[indices_to_remove] = float('-inf')

  # TODO: Sample from the masked logits
  probs = F.softmax(next_token_logits, dim=-1)
  next_tokens = torch.multinomial(probs, num_samples=1).squeeze(-1)

  return next_tokens


set_seed()
generations = decode(dev_prompts, max_len=20, method='topp', p=0.7)
print_generations(dev_prompts, generations)

['Ryan was called by his friend to skip work one day.'] ==> ["\n\nKiddie said he also didn't know if he was working out or not, and"]
['Ryan was called by his friend to skip work one day.'] ==> [' On the day of the attack, he took the opportunity to share a beautiful moment with her, a']
['Ryan was called by his friend to skip work one day.'] ==> [' When he arrived at work, the new tenant was coming in with a pile of trash.\n\n']
['Ryan was called by his friend to skip work one day.'] ==> [' "No, my boyfriend doesn\'t do that," he said, before jogging out to his room']
['Ryan was called by his friend to skip work one day.'] ==> [' He also sat in a wheelchair at his hospital bed. In the room was a young woman who looked']
['Ryan was called by his friend to skip work one day.'] ==> [" The rookie's parents said he was talking to his father and asking him to help him.\n\n"]
['Ryan was called by his friend to skip work one day.'] ==> [" Then he goes back to work. He can't afford to do it. S

### 1.5: Evaluation

Run the following cell to obtain the evaluation results, which you should include in your writeup.
Also don't forget to answer the questions.

In [14]:
prompts = [item['prompt'] for item in test_data][:10]
GENERATIONS_PER_PROMPT = 10
MAX_LEN = 100

for experiment in ['greedy', 'sample', 'temperature', 'topk', 'topp']:
  generations = []
  for prompt in tqdm(prompts):
    generations += decode([prompt] * GENERATIONS_PER_PROMPT, max_len=MAX_LEN, method=experiment)
  evaluate(generations, experiment)

  0%|          | 0/10 [00:00<?, ?it/s]

  0%|          | 0/13 [00:00<?, ?it/s]

greedy
perplexity = 2.08
fluency = 0.78
diversity = 0.01, 0.02, 0.03



  0%|          | 0/10 [00:00<?, ?it/s]

  0%|          | 0/13 [00:00<?, ?it/s]

...

  0%|          | 0/13 [00:00<?, ?it/s]

topk
perplexity = 12.24
fluency = 0.74
diversity = 0.26, 0.75, 0.96



  0%|          | 0/10 [00:00<?, ?it/s]

  0%|          | 0/13 [00:00<?, ?it/s]

topp
perplexity = 12.40
fluency = 0.72
diversity = 0.29, 0.76, 0.96



### Discussion
- Q1.1: In greedy decoding, what do you observe when generating 10 times from the test prompt?

- Q1.2: In vanilla sampling, what do you observe when generating 10 times from the test prompt?

- Q1.3: In temperature sampling, play around with the value of temperature $t$. Which value of $t$ makes it equivalent to greedy decoding? Which value of $t$ makes it equivalent to vanilla sampling?

- Q1.4: In top-$p$ sampling, play around with the value of $p$. Which value of $p$ makes it equivalent to greedy decoding? Which value of $p$ makes it equivalent to vanilla sampling?

- Q1.5: In top-k sampling, play around with the value of k. Which value of k makes it equivalent to greedy decoding? Which value of k makes it equivalent to vanilla sampling?

- Q1.6: Report the evaluation metrics (perplexity, fluency, diversity) of all 5 decoding methods. Which methods have the best and worst perplexity? Fluency? Diversity?


## Section 2: Applying Large Language Models to Few Shot Math Reasoning

In [15]:
!uv pip install -q vllm # restart runtime session after install requirements



In [16]:
import os
os.environ["HF_HOME"] = "/content/.cache/huggingface" # set the cache directory to personal disk to avoid frequent downloads



In [17]:
!pip install bitblas>=0.1.0

In [18]:
from vllm import LLM, SamplingParams
model_id = "Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4"
llm = LLM(model=model_id, enforce_eager=True, quantization="gptq", gpu_memory_utilization=0.9)



INFO 05-02 14:43:47 [importing.py:53] Triton module has been replaced with a placeholder.
INFO 05-02 14:43:48 [__init__.py:239] Automatically detected platform cuda.


config.json:   0%|          | 0.00/1.26k [00:00<?, ?B/s]

INFO 05-02 14:44:23 [config.py:717] This model supports multiple tasks: {'reward', 'embed', 'score', 'generate', 'classify'}. Defaulting to 'generate'.
INFO 05-02 14:44:24 [gptq_bitblas.py:168] Detected that the model can run with gptq_bitblas, however you specified quantization=gptq explicitly, so forcing gptq. Use quantization=gptq_bitblas for faster inference
WARNING 05-02 14:44:24 [config.py:830] gptq quantization is not fully optimized yet. The speed can be slower than non-quantized models.
WARNING 05-02 14:44:24 [arg_utils.py:1658] Compute Capability < 8.0 is not supported by the V1 Engine. Falling back to V0. 
WARNING 05-02 14:44:24 [cuda.py:93] To see benefits of async output processing, enable CUDA graph. Since, enforce-eager is enabled, async output processor cannot be used
INFO 05-02 14:44:24 [llm_engine.py:240] Initializing a V0 LLM engine (v0.8.5) with config: model='Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4', speculative_config=None, tokenizer='Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4

tokenizer_config.json:   0%|          | 0.00/7.30k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/2.78M [00:00<?, ?B/s]

...

model-00001-of-00002.safetensors:   0%|          | 0.00/4.00G [00:00<?, ?B/s]

INFO 05-02 14:45:19 [weight_utils.py:281] Time spent downloading weights for Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4: 48.326936 seconds


model.safetensors.index.json:   0%|          | 0.00/75.4k [00:00<?, ?B/s]

Loading safetensors checkpoint shards:   0% Completed | 0/2 [00:00<?, ?it/s]


INFO 05-02 14:45:38 [loader.py:458] Loading weights took 18.83 seconds
INFO 05-02 14:45:38 [model_runner.py:1140] Model loading took 5.2040 GiB and 67.959221 seconds
INFO 05-02 14:46:02 [worker.py:287] Memory profiling takes 23.07 seconds
INFO 05-02 14:46:02 [worker.py:287] the current vLLM instance can use total_gpu_memory (14.74GiB) x gpu_memory_utilization (0.90) = 13.27GiB
INFO 05-02 14:46:02 [worker.py:287] model weights take 5.20GiB; non_torch_memory takes 0.02GiB; PyTorch activation peak memory takes 4.47GiB; the rest of the memory reserved for KV Cache is 3.57GiB.
INFO 05-02 14:46:03 [executor_base.py:112] # cuda blocks: 4176, # CPU blocks: 4681
INFO 05-02 14:46:03 [executor_base.py:117] Maximum concurrency for 32768 tokens per request: 2.04x
INFO 05-02 14:46:08 [llm_engine.py:437] init engine (profile, create kv cache, warmup model) took 29.78 seconds


In [19]:
######################################################
#  The following helper code is given to you.
######################################################

from openai import OpenAI
from transformers import AutoTokenizer

class VLLMClient:
    def __init__(self, model_id, **kwargs):
      self.model_id = model_id

    def __call__(self, prompt: str, **kwargs):
      response = llm.generate(
            prompts=prompt,
            sampling_params=SamplingParams(
                temperature=kwargs.get("temperature", 0.2),
                max_tokens=kwargs.get("max_tokens", 256),
            )
      )
      return response[0].outputs[0].text
model = VLLMClient(model_id)
model("San Francisco is a", max_tokens=42)



Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

' city of neighborhoods, each with its own distinct character. Here are some of the most popular neighborhoods in San Francisco, along with a brief description of what makes them special:\n\n  1. The Mission: Known'

In [20]:
######################################################
#  The following helper code is given to you.
######################################################

GSM_EXAMPLARS = [
    {
        "question": "There are 15 trees in the grove. Grove workers will plant trees in the grove today. After they are done, there will be 21 trees. How many trees did the grove workers plant today?",
        "cot_answer": "There are 15 trees originally. Then there were 21 trees after some more were planted. So there must have been 21 - 15 = 6. So the answer is 6.",
        "short_answer": "6"
    },
    {
        "question": "If there are 3 cars in the parking lot and 2 more cars arrive, how many cars are in the parking lot?",
        "cot_answer": "There are originally 3 cars. 2 more cars arrive. 3 + 2 = 5. So the answer is 5.",
        "short_answer": "5"
    },
    {
        "question": "Leah had 32 chocolates and her sister had 42. If they ate 35, how many pieces do they have left in total?",
        "cot_answer": "Originally, Leah had 32 chocolates. Her sister had 42. So in total they had 32 + 42 = 74. After eating 35, they had 74 - 35 = 39. So the answer is 39.",
        "short_answer": "39"
    },
    {
        "question": "Jason had 20 lollipops. He gave Denny some lollipops. Now Jason has 12 lollipops. How many lollipops did Jason give to Denny?",
        "cot_answer": "Jason started with 20 lollipops. Then he had 12 after giving some to Denny. So he gave Denny 20 - 12 = 8. So the answer is 8.",
        "short_answer": "8"
    },
    {
        "question": "Shawn has five toys. For Christmas, he got two toys each from his mom and dad. How many toys does he have now?",
        "cot_answer": "Shawn started with 5 toys. If he got 2 toys each from his mom and dad, then that is 4 more toys. 5 + 4 = 9. So the answer is 9.",
        "short_answer": "9"
    },
    {
        "question": "There were nine computers in the server room. Five more computers were installed each day, from monday to thursday. How many computers are now in the server room?",
        "cot_answer": "There were originally 9 computers. For each of 4 days, 5 more computers were added. So 5 * 4 = 20 computers were added. 9 + 20 is 29. So the answer is 29.",
        "short_answer": "29"
    },
    {
        "question": "Michael had 58 golf balls. On tuesday, he lost 23 golf balls. On wednesday, he lost 2 more. How many golf balls did he have at the end of wednesday?",
        "cot_answer": "Michael started with 58 golf balls. After losing 23 on tuesday, he had 58 - 23 = 35. After losing 2 more, he had 35 - 2 = 33 golf balls. So the answer is 33.",
        "short_answer": "33"
    },
    {
        "question": "Olivia has $23. She bought five bagels for $3 each. How much money does she have left?",
        "cot_answer": "Olivia had 23 dollars. 5 bagels for 3 dollars each will be 5 x 3 = 15 dollars. So she has 23 - 15 dollars left. 23 - 15 is 8. So the answer is 8.",
        "short_answer": "8"
    }
]



In [21]:
!mkdir -p data
!wget -q -O data/gsm8k.jsonl https://raw.githubusercontent.com/ranpox/comp3361-spring2025/refs/heads/main/assignments/A3/data/gsm8k.jsonl
!wget -q -O data/simpleqa.jsonl https://raw.githubusercontent.com/ranpox/comp3361-spring2025/refs/heads/main/assignments/A3/data/simpleqa.jsonl
!wget -q -O data/math.jsonl https://raw.githubusercontent.com/ranpox/comp3361-spring2025/refs/heads/main/assignments/A3/data/math.jsonl
!wget -q -O data/gaia.jsonl https://raw.githubusercontent.com/ranpox/comp3361-spring2025/refs/heads/main/assignments/A3/data/gaia.jsonl




In [22]:
######################################################
#  The following helper code is given to you.
######################################################

import json

def load_eval_data(task):
    with open(f"data/{task}.jsonl", "r") as f:
        return [json.loads(line) for line in f]

tasks = ["gsm8k", "simpleqa", "math", "gaia"]

for task in tasks:
    print(f"Example of {task} dataset:")
    print(json.dumps(load_eval_data(task)[0], indent=4))



Example of gsm8k dataset:
{
    "question": "Janet\u2019s ducks lay 16 eggs per day. She eats three for breakfast every morning and bakes muffins for her friends every day with four. She sells the remainder at the farmers' market daily for $2 per fresh duck egg. How much in dollars does she make every day at the farmers' market?",
    "source": "GSM8K",
    "true_answer": "18",
    "true_reasoning": "Janet sells 16 - 3 - 4 = <<16-3-4=9>>9 duck eggs a day.\nShe makes 9 * 2 = $<<9*2=18>>18 every day at the farmer\u2019s market."
}
Example of simpleqa dataset:
{
    "question": "What year was the municipality of Ramiriqu\u00ed, Boyac\u00e1, Colombia, founded?",
    "source": "SimpleQA",
    "true_answer": "1541",
    "true_reasoning": "['https://en.wikipedia.org/wiki/Ramiriqu%C3%AD', 'https://en.wikipedia.org/wiki/Ramiriqu%C3%AD', 'https://www.ramiriqui-boyaca.gov.co/municipio/nuestro-municipio', 'https://www.familysearch.org/es/wiki/Ramiriqu%C3%AD,_M%C3%A1rquez,_Boyac%C3%A1,_Colombia_-_G

In [23]:
######################################################
#  The following helper code is given to you.
######################################################

import os
import datetime
import threading
from pathlib import Path
from tqdm.notebook import tqdm
from concurrent.futures import ThreadPoolExecutor, as_completed

APPEND_ANSWER_LOCK = threading.Lock()

def append_answer(entry: dict, jsonl_file: str) -> None:
    jsonl_file = Path(jsonl_file)
    jsonl_file.parent.mkdir(parents=True, exist_ok=True)
    with APPEND_ANSWER_LOCK, open(jsonl_file, "a", encoding="utf-8") as fp:
        fp.write(json.dumps(entry) + "\n")
    assert os.path.exists(jsonl_file), "File not found!"

def answer_single_question(example, agent, answers_file, action_type):
    augmented_question = example["question"]
    if example["source"] == "SimpleQA":
        augmented_question += " Answer with only the final number."
    if example["source"] == "MATH":
        augmented_question += " Write code, not latex."

    start_time = datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S")

    answer = str(agent.run(augmented_question))

    end_time = datetime.datetime.now().strftime("%Y-%m-%d %H:%M:%S")
    annotated_example = {
        "model_id": model.model_id,
        "agent_action_type": action_type,
        "question": augmented_question,
        "original_question": example["question"],
        "answer": answer,
        "true_answer": example["true_answer"],
        "source": example["source"],
        "start_time": start_time,
        "end_time": end_time,
    }
    append_answer(annotated_example, answers_file)

def answer_questions(
    task,
    agent,
    action_type: str = "vanilla",
    answers_file: str = None,
    parallel_workers: int = 4,
):
    eval_data = load_eval_data(task)

    print(f"Starting processing and writing output to '{answers_file}'")

    answered_questions = []
    if os.path.exists(answers_file):
        with open(answers_file, "r") as f:
            for line in f:
                answered_questions.append(json.loads(line)["original_question"])

    examples_todo = [example for example in eval_data if example["question"] not in answered_questions]


    for i, example in enumerate(tqdm(examples_todo)):
        answer_single_question(example, agent, answers_file, action_type)



In [24]:
!wget -q -O eval_utils.py https://raw.githubusercontent.com/ranpox/comp3361-spring2025/refs/heads/main/assignments/A3/evaluate.py

!pip install tqdm pandas


In [26]:
from eval_utils import score_answers
class FewShotReasoner:
    def __init__(self, model, n_shots):
        self.model = model
        self.n_shots = n_shots

    def run(self, task):
        prompt = self.build_input(task)
        response = self.model(prompt, max_tokens=256, temperature=0.2)
        return self.extract_answer(response)

    def build_input(self, task):
        prompt = "Answer the following math word problems step by step. At the end, conclude with 'The answer is X.' where X is the final numerical answer.\n\n"

        for example in GSM_EXAMPLARS[:self.n_shots]:
            prompt += f"Question: {example['question']}\n"
            prompt += f"Answer: {example['short_answer']}\n\n"

        prompt += f"Question: {task}\n"
        prompt += "Answer:"
        return prompt

    def extract_answer(self, response):
        import re
        match = re.search(r'The answer is (\d+\.?\d*).', response)
        if match:
            return match.group(1)
        numbers = re.findall(r'\d+\.?\d*', response)
        if numbers:
            return numbers[-1]
        return response.strip()

def run_gsm8k_fewshot_reasoner(task="gsm8k", model_id=model_id, action_type="fewshot"):
    reasoner_answers_file = f"output/{model_id.replace('/', '__')}__{action_type}__{task}.jsonl"
    chat_agent = FewShotReasoner(model, 8)
    answer_questions(task, chat_agent, action_type, reasoner_answers_file)
    df = score_answers([reasoner_answers_file])
    print(df)

run_gsm8k_fewshot_reasoner()

Starting processing and writing output to 'output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__fewshot__gsm8k.jsonl'


  0%|          | 0/50 [00:00<?, ?it/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

...

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__fewshot__gsm8k.jsonl


Processing tasks:   0%|          | 0/1 [00:00<?, ?it/s]

                             model_id agent_action_type source   acc
0  Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4           fewshot  GSM8K  0.08


In [27]:
import re

class FewShotCoTReasoner:
    def __init__(self, model, n_shots):
        self.model = model
        self.n_shots = n_shots

    def run(self, task):
        prompt = self.build_input(task)
        response = self.model(prompt)

        return self.extract_final_answer(response)

    def build_input(self, task):
        prompt_lines = ["Answer the following questions with step-by-step reasoning:"]

        for example in GSM_EXAMPLARS[:self.n_shots]:
          prompt_lines.append(f"Question: {example['question']}")
          prompt_lines.append(f"Answer: {example['cot_answer']}")

        prompt_lines.append(f"Question: {task}")
        prompt_lines.append("Answer:")

        return "\n".join(prompt_lines)

    def extract_final_answer(self, cot_response):
        matches = re.findall(r'(?:So |The |)(?:answer|Answer)(?: is|:)? (\d+(?:\.\d+)?)', cot_response)
        if matches:
            return matches[-1]
        return cot_response.strip()

def run_gsm8k_fewshot_cot_reasoner(task="gsm8k", model_id=model_id, action_type="fewshot_cot"):
    reasoner_answers_file = f"output/{model_id.replace('/', '__')}__{action_type}__{task}__cot.jsonl"
    chat_agent = FewShotCoTReasoner(model, 8)
    answer_questions(task, chat_agent, action_type, reasoner_answers_file)
    df = score_answers([reasoner_answers_file])
    print(df)

run_gsm8k_fewshot_cot_reasoner()



Starting processing and writing output to 'output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__fewshot_cot__gsm8k__cot.jsonl'


  0%|          | 0/50 [00:00<?, ?it/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

...

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__fewshot_cot__gsm8k__cot.jsonl


Processing tasks:   0%|          | 0/1 [00:00<?, ?it/s]

                             model_id agent_action_type source   acc
0  Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4       fewshot_cot  GSM8K  0.84


## Section 3:Building and Evaluating LLM Agents

In [28]:
######################################################
#  The following helper code is given to you.
######################################################

from transformers import AutoTokenizer
class ChatAgent:
    def __init__(self, model):
        self.model = model
        self.tokenizer = AutoTokenizer.from_pretrained(model.model_id)

    def run(self, task):
        prompt = self.build_input(task)
        return self.model(prompt=prompt)

    def build_input(self, task):
        messages = [{"role": "user", "content": task}]
        return self.tokenizer.apply_chat_template(messages, tokenize=False, add_generation_prompt=True)

action_type="vanilla"
chat_agent_answers_files = {}
for task in ["simpleqa", "math", "gaia"]:
    chat_agent_answers_file = f"output/{model_id.replace('/', '__')}__{action_type}__{task}.jsonl"
    chat_agent = ChatAgent(model)
    answer_questions(task, chat_agent, action_type, chat_agent_answers_file, parallel_workers=8)
    chat_agent_answers_files[task] = chat_agent_answers_file
score_answers(chat_agent_answers_files.values())



Starting processing and writing output to 'output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__vanilla__simpleqa.jsonl'


  0%|          | 0/50 [00:00<?, ?it/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

...

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__vanilla__simpleqa.jsonl
output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__vanilla__math.jsonl
output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__vanilla__gaia.jsonl


/content/eval_utils.py:89: UserWarning: Answer lists have different lengths, returning False.
  warnings.warn("Answer lists have different lengths, returning False.", UserWarning)
/content/eval_utils.py:89: UserWarning: Answer lists have different lengths, returning False.
  warnings.warn("Answer lists have different lengths, returning False.", UserWarning)


Processing tasks:   0%|          | 0/3 [00:00<?, ?it/s]

model_id agent_action_type    source      acc
0  Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4           vanilla      GAIA  0.03125
1  Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4           vanilla  SimpleQA  0.02000
2  Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4           vanilla      MATH  0.18000

In [29]:
######################################################
#  The following helper code is given to you.
######################################################

from io import StringIO
import sys
import inspect
from typing import Any, Dict, Union, Optional, Tuple, List

class Tool:
    name: str
    description: str
    inputs: Dict[str, Dict[str, Union[str, type, bool]]]
    output_type: str

    def __init__(self, *args, **kwargs):
        self.is_initialized = False

    def forward(self, *args, **kwargs):
        return NotImplementedError("Write this method in your subclass of `Tool`.")

    def __call__(self, *args, **kwargs):
        outputs = self.forward(*args, **kwargs)
        return outputs

    def to_dict(self) -> dict:
        return {
            "type": "function",
            "function": {
                "name": self.name,
                "description": self.description,
                "parameters": {
                    "type": "object",
                    "properties": self.inputs,
                    "required": list(self.inputs.keys()),
                },
            },
            "strict": True
        }




In [30]:
######################################################
#  The following helper code is given to you.
######################################################

from typing import Any

class FinalAnswerTool(Tool):
    name = "final_answer"
    description = "Provides a final answer to the given problem. Make sure to use this tool to provide the final answer at the end of the task."
    inputs = {"answer": {"type": "any", "description": "The final answer to the problem"}}
    output_type = "any"

    def forward(self, answer: Any) -> Any:
        return answer




In [31]:
######################################################
#  The following helper code is given to you.
######################################################

final_answer_tool = FinalAnswerTool()
final_answer_tool("Hello, world!")

tools = [
    final_answer_tool.to_dict()
]

messages = [
    {"role": "user", "content": "What year was the municipality of Ramiriqu\u00ed, Boyac\u00e1, Colombia, founded?  Answer with only the final number."}
]
tokenizer = AutoTokenizer.from_pretrained(model.model_id)
print("="*10 + "Input Prompt" + "="*10 + "\n")
input_prompt = tokenizer.apply_chat_template(messages, tools=tools, tokenize=False, add_generation_prompt=True)
print("="*10 + "Response" + "="*10 + "\n")
response = model(tokenizer.apply_chat_template(messages, tools=tools, tokenize=False, add_generation_prompt=True))
print("\n\n" + response)





==========Input Prompt==========

==========Response==========



Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]



<tool_call>
{"name": "final_answer", "arguments": {"answer": 1819}}
</tool_call>


In [32]:
class GoogleSearchTool(Tool):
    name = "web_search"
    description = """Performs a google web search for your query then returns a string of the top search results."""
    inputs = {
        "query": {"type": "string", "description": "The search query to perform."},
    }
    output_type = "string"


    def __init__(self, provider: str = "serper", api_key: str = None):
        super().__init__()
        self.provider = provider
        self.api_key = api_key or os.getenv("SERPER_API_KEY")
        self.is_initialized = True


    def forward(self, query: str) -> str:
        url = "https://google.serper.dev/search"
        headers = {
            'X-API-KEY': self.api_key,
            'Content-Type': 'application/json'
        }
        payload = json.dumps({"q":query, "gl":"us", "hl":"en", "num":3})

        try:
          response = requests.post(url, headers=headers, data=payload)
          response.raise_for_status()
          results = response.json()

          if 'organic' not in results:
            return "No results found"

          output = []
          for item in results['organic'][:3]:
                output.append(
                    f"Title: {item.get('title', 'N/A')} "
                    f"Link: {item.get('link', 'N/A')} "
                    f"Snippet: {item.get('snippet', 'N/A')}"
                )

          return output if output else "No results found"

        except Exception as e:
          return f"Search error: {str(e)}"




In [33]:
import requests
import os
import json
from typing import Dict, Any
os.environ["SERPER_API_KEY"] = "ca8c395914301ca5a1ea8a6d13447eae6ae3a82f" # remember to remove your key for submission
google_search_tool = GoogleSearchTool()
google_search_tool("Space Exploration Technologies Corp.")



['Title: SpaceX Link: https://www.spacex.com/ Snippet: SpaceX designs, manufactures and launches advanced rockets and spacecraft. The company was founded in 2002 to revolutionize space technology, with the ultimate',
 'Title: SpaceX - Wikipedia Link: https://en.wikipedia.org/wiki/SpaceX Snippet: Space Exploration Technologies Corp., commonly referred to as SpaceX, is an American space technology company headquartered at the Starbase development site ...']

In [34]:
!uv pip install markdownify requests beautifulsoup4 readability-lxml lxml_html_clean

Using Python 3.11.12 environment at: /usr
Resolved 15 packages in 250ms
⠙ Preparing packages... (0/3)
⠙ Preparing packages... (0/3)
⠙ Preparing packages... (0/3)
lxml-html-clean ------------------------------ 13.85 KiB/13.85 KiB
⠙ Preparing packages... (0/3)
⠙ Preparing packages... (0/3)
⠙ Preparing packages... (0/3)
cssselect  ------------------------------ 16.00 KiB/18.35 KiB
⠙ Preparing packages... (0/3)
cssselect  ------------------------------ 18.35 KiB/18.35 KiB
⠙ Preparing packages... (0/3)
⠙ Preparing packages... (0/3)
⠙ Preparing packages... (0/3)
Prepared 3 packages in 19ms
Installed 3 packages in 8ms
 + cssselect==1.3.0
 + lxml-html-clean==0.4.2
 + readability-lxml==0.8.1


In [35]:
class VisitWebpageTool(Tool):
    name = "visit_webpage"
    description = "Visits a webpage and extracts clean text content, optimized for Wikipedia"
    inputs = {"url": {"type": "string", "description": "The URL to visit"}}
    output_type = "string"

    def __init__(self, max_output_length: int = 10000):
        super().__init__()
        self.max_output_length = max_output_length
        self.headers = {
            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36'
        }

    def forward(self, url: str) -> str:
        try:
            import requests
            from bs4 import BeautifulSoup
            import re
            from readability import Document
            from requests.exceptions import RequestException
        except ImportError:
            raise ImportError("Please install: pip install requests beautifulsoup4 readability-lxml")

        try:
            response = requests.get(url, headers=self.headers, timeout=15)
            response.raise_for_status()

            if 'wikipedia.org' in url:
                soup = BeautifulSoup(response.text, 'html.parser')

                content = soup.find(id='mw-content-text')
                if not content:
                    return "Could not find main content"

                for element in content.find_all(['script', 'style', 'table', 'figure', 'sup']):
                    element.decompose()


                text = content.get_text()
                text = re.sub(r'\n{3,}', '\n\n', text)
                text = re.sub(r'\[\d+\]', '', text)
                text = text.strip()

                if len(text) > self.max_output_length:
                    text = text[:self.max_output_length] + "... [truncated]"
                return text

            doc = Document(response.text)
            soup = BeautifulSoup(doc.summary(), 'html.parser')
            text = soup.get_text()
            text = re.sub(r'\s+', ' ', text).strip()

            if len(text) > self.max_output_length:
                text = text[:self.max_output_length] + "... [truncated]"
            return text

        except requests.exceptions.Timeout:
            return "The request timed out. Please try again later or check the URL."
        except RequestException as e:
            return f"Error fetching the webpage: {str(e)}"
        except Exception as e:
            return f"An unexpected error occurred: {str(e)}"




In [36]:
visit_page_tool = VisitWebpageTool()
visit_page_tool("https://plato.stanford.edu/entries/consciousness/")



"Questions about the nature of conscious awareness have likely been asked for as long as there have been humans. Neolithic burial practices appear to express spiritual beliefs and provide early evidence for at least minimally reflective thought about the nature of human consciousness (Pearson 1999, Clark and Riel-Salvatore 2001). Preliterate cultures have similarly been found invariably to embrace some form of spiritual or at least animist view that indicates a degree of reflection about the nature of conscious awareness. Nonetheless, some have argued that consciousness as we know it today is a relatively recent historical development that arose sometime after the Homeric era (Jaynes 1974). According to this view, earlier humans including those who fought the Trojan War did not experience themselves as unified internal subjects of their thoughts and actions, at least not in the ways we do today. Others have claimed that even during the classical period, there was no word of ancient Gre

In [44]:

import re
import json
from typing import List, Dict, Any, Callable, Optional

system_prompt = """
You are an expert assistant who can solve any task using tool calls. You will be given a task to solve as best you can.
To do so, you have been given access to some tools.

Here are the rules you should always follow to solve your task:
1. ALWAYS provide a tool call, else you will fail.
2. Always use the right arguments for the tools. Never use variable names as the action arguments, use the value instead.
3. Call a tool only when needed: do not call the search agent if you do not need information, try to solve the task yourself.
If no tool call is needed, use final_answer tool to return your answer.
4. Never re-do a tool call that you previously did with the exact same parameters.
"""


class ToolCallAgent:
    """
    A minimal agent that uses a language model to interact with tools
    based on the ToolCallingAgent pattern.
    """
    def __init__(
        self,
        model: Callable,
        tools: List[Tool],
        max_steps: int = 5,
        final_answer_tool_name: str = "final_answer",
        print_log: bool = True
    ):
        self.model = model
        self.tokenizer = AutoTokenizer.from_pretrained(model.model_id)
        self.tools_definitions = [tool.to_dict() for tool in tools]
        self.tool_executors = {tool.name: tool for tool in tools}
        self.max_steps = max_steps
        self.final_answer_tool_name = final_answer_tool_name

        self.log_func = lambda x: print(x) if print_log else lambda _: None

        # Validate that the final answer tool has an executor
        if self.final_answer_tool_name not in self.tool_executors:
            raise ValueError(f"Executor for final answer tool '{self.final_answer_tool_name}' not found in tool_executors.")

    def _execute_tool(self, tool_name: str, parsed_args: Any) -> str:
        executor = self.tool_executors[tool_name]
        try:
            self.log_func(f"Executing tool '{tool_name}' with args: {parsed_args}")

            if isinstance(parsed_args, dict):
              tool_result = executor(**parsed_args)
            else:
              tool_result = executor(parsed_args)

            self.log_func(f"Tool '{tool_name}' executed. Output: {tool_result}")
            # The final_answer tool itself returns the value, we don't stringify it here yet
            return tool_result

        except Exception as e:
            print(f"Error executing tool '{tool_name}' with args {parsed_args}: {e}")
            # Return the error message as the observation
            return f"Error during execution of tool '{tool_name}': {e}"

    def _parse_tool_arguments(self, content: str):
        """Try parse the tool calls."""

        try:
            tool_call = json.loads(content)
            if isinstance(tool_call, dict) and "name" in tool_call:
                return tool_call
        except json.JSONDecodeError:
            pass


        patterns = [
            r'<tool_call>(.*?)</tool_call>',
            r'Final answer:?\s*(\d+)',
            r'answer is (\d+)'
        ]

        for pattern in patterns:
            match = re.search(pattern, content, re.DOTALL)
            if match:
                if pattern.startswith('<tool_call'):
                    try:
                        return json.loads(match.group(1))
                    except:
                        continue
                else:
                    return {
                        "name": self.final_answer_tool_name,
                        "arguments": {"answer": match.group(1)}
                    }

        return None


    def run(self, task: str) -> Any:
        """
        Runs the agent loop starting with the initial messages.

        Args:
            task: The initial user prompt.

        Returns:
            The final answer extracted from the final_answer tool call,
            or None if max_steps is reached or an error occurs.
        """


        messages = [
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": task}
        ]

        self.log_func(f"Starting agent run with max_steps={self.max_steps}")
        self.log_func("Initial messages:")
        self.log_func(json.dumps(messages, indent=2))
        self.log_func("-" * 30)

        for step in range(self.max_steps):
            self.log_func(f"--- Step {step + 1} ---")

        messages = [
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": task}
        ]

        for step in range(self.max_steps):
            prompt = self.tokenizer.apply_chat_template(
                messages,
                tools=self.tools_definitions,
                tokenize=False,
                add_generation_prompt=True
            )

            response = self.model(prompt)
            tool_call = self._parse_tool_arguments(response)

            if not tool_call:
                if step == 0:  # First attempt failed
                    return None
                continue

            # Execute tool
            result = self._execute_tool(tool_call["name"], tool_call["arguments"])

            if tool_call["name"] == self.final_answer_tool_name:
                if self._validate_answer(result):
                    return result
                continue

            # Update conversation
            messages.extend([
                {"role": "assistant", "content": response},
                {"role": "tool", "name": tool_call["name"], "content": str(result)}
            ])

        return None




In [45]:
######################################################
#  The following helper code is given to you.
######################################################

def run_simpleqa_tool_calling_agent(task="simpleqa", model_id=model_id, action_type="tool_calling"):
    search_agent_answers_file = f"output/{model_id.replace('/', '__')}__{action_type}__{task}.jsonl"
    search_agent = ToolCallAgent(
        model=model,
        tools=[GoogleSearchTool(), VisitWebpageTool(), FinalAnswerTool()],
        max_steps=10
    )
    answer_questions(task, search_agent, action_type, search_agent_answers_file)
    df = score_answers([search_agent_answers_file])
    print(df)

run_simpleqa_tool_calling_agent()

Starting processing and writing output to 'output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__tool_calling__simpleqa.jsonl'


0it [00:00, ?it/s]

output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__tool_calling__simpleqa.jsonl


Processing tasks:   0%|          | 0/1 [00:00<?, ?it/s]

                             model_id agent_action_type    source   acc
0  Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4      tool_calling  SimpleQA  0.16


In [41]:
!wget -q -O local_python_executor.py https://raw.githubusercontent.com/ranpox/comp3361-spring2025/refs/heads/main/assignments/A3/local_python_executor.py

In [42]:
######################################################
#  The following helper code is given to you.
######################################################

from local_python_executor import (
    BASE_BUILTIN_MODULES,
    BASE_PYTHON_TOOLS,
    evaluate_python_code,
)


class PythonInterpreterTool(Tool):
    name = "python_interpreter"
    description = "This is a tool for evaluating python code. It can be used to perform calculations. To generate valid Python code, first draft your code in Markdown using ```python```, then write it as a one-line string in the `code` field"
    inputs = {
        "code": {
            "type": "string",
            "description": "The python code to run in interpreter",
        }
    }
    output_type = "string"

    def __init__(self, *args, authorized_imports=None, **kwargs):
        if authorized_imports is None:
            self.authorized_imports = list(set(BASE_BUILTIN_MODULES))
        else:
            self.authorized_imports = list(set(BASE_BUILTIN_MODULES) | set(authorized_imports))
        self.inputs = {
            "code": {
                "type": "string",
                "description": (
                    "The code snippet to evaluate. All variables used in this snippet must be defined in this same snippet, "
                    f"else you will get an error. This code can only import the following python libraries: {self.authorized_imports}."
                ),
            }
        }
        self.base_python_tools = BASE_PYTHON_TOOLS
        self.python_evaluator = evaluate_python_code
        super().__init__(*args, **kwargs)

    def forward(self, code: str) -> str:
        state = {}
        output = str(
            self.python_evaluator(
                code,
                state=state,
                static_tools=self.base_python_tools,
                authorized_imports=self.authorized_imports,
            )  # The second element is boolean is_final_answer
        )
        return f"Stdout:\n{str(state['_print_outputs'])}\nOutput: {output}"

In [43]:
######################################################
#  The following helper code is given to you.
######################################################

from eval_utils import score_answers

def run_math_tool_calling_agent(task="math", model_id=model_id, action_type="tool_calling"):
    math_agent_answers_file = f"output/{model_id.replace('/', '__')}__{action_type}__{task}.jsonl"
    math_agent = ToolCallAgent(
        model=model,
        tools=[PythonInterpreterTool(authorized_imports=["numpy", "sympy"]), FinalAnswerTool()],
        max_steps=10
    )
    answer_questions(task, math_agent, action_type, math_agent_answers_file)
    df = score_answers([math_agent_answers_file])
    print(df)

run_math_tool_calling_agent()

Starting processing and writing output to 'output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__tool_calling__math.jsonl'


  0%|          | 0/50 [00:00<?, ?it/s]

Starting agent run with max_steps=10
Initial messages:
[
  {
    "role": "system",
    "content": "\nYou are an expert assistant who can solve any task using tool calls. You will be given a task to solve as best you can.\nTo do so, you have been given access to some tools.\n\nHere are the rules you should always follow to solve your task:\n1. ALWAYS provide a tool call, else you will fail.\n2. Always use the right arguments for the tools. Never use variable names as the action arguments, use the value instead.\n3. Call a tool only when needed: do not call the search agent if you do not need information, try to solve the task yourself.\nIf no tool call is needed, use final_answer tool to return your answer.\n4. Never re-do a tool call that you previously did with the exact same parameters.\n"
  },
  {
    "role": "user",
    "content": "Below is a magic square, meaning that the sum of the numbers in each row, in each column, and in each of the $2$ main diagonals are equal. What is the v

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Model response:
To solve this problem, we need to find the value of n such that the sum of the numbers in each row, each column, and each of the two main diagonals are equal. We can set up equations based on the given magic square and solve for n.

Let's start by setting up the equations for the rows, columns, and diagonals. We can then solve these equations to find the value of n.

Equations for the rows:
1. (n-3) + 3 + (n+1) = 2n + 1
2. (n+2) + (2n-9) + 1 = 3n - 6
3. 2 + n + (n-1) = 2n + 1

Equations for the columns:
1. (n-3) + (n+2) + 2 = 2n + 1
2. 3 + (2n-9) + n = 3n - 6
3. (n+1) + 1 + (n-1) = 2n + 1

Equations for the diagonals:
1. (n-3) + (2n-9)
No valid tool call found in response
Starting agent run with max_steps=10
Initial messages:
[
  {
    "role": "system",
    "content": "\nYou are an expert assistant who can solve any task using tool calls. You will be given a task to solve as best you can.\nTo do so, you have been given access to some tools.\n\nHere are the rules you sho

...

Model response:
Given the constraints, we will use a numerical method available in the allowed libraries to approximate the solution. Since we cannot import fsolve from scipy, we will use a numerical solver from sympy to find the root of the equation.

Let's use sympy's `nsolve` function to find the numerical solution.
<tool_call>
{"name": "python_interpreter", "arguments": {"code": "from sympy import symbols, Eq, nsolve; x = symbols('x'); eq = Eq(3**(2*x) + 19, 10**x); nsolve(eq, 1)"}}
</tool_call>
Executing tool 'python_interpreter' with args: {'code': "from sympy import symbols, Eq, nsolve; x = symbols('x'); eq = Eq(3**(2*x) + 19, 10**x); nsolve(eq, 1)"}
Tool 'python_interpreter' executed. Output: Stdout:

Output: 2.00000000000000
------------------------------
--- Step 6 ---


Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Model response:
The numerical solution to the equation \(3^{2x} + 19 = 10^x\) is approximately \(x = 2.000\).

<tool_call>
{"name": "final_answer", "arguments": {"answer": 2.000}}
</tool_call>
Executing tool 'final_answer' with args: {'answer': 2.0}
Tool 'final_answer' executed. Output: 2.0
Final answer received: 2.0
output/Qwen__Qwen2.5-7B-Instruct-GPTQ-Int4__tool_calling__math.jsonl


Processing tasks:   0%|          | 0/1 [00:00<?, ?it/s]

                             model_id agent_action_type source  acc
0  Qwen/Qwen2.5-7B-Instruct-GPTQ-Int4      tool_calling   MATH  0.3


In [ ]:
######################################################
#  The following helper code is given to you.
######################################################

from eval_utils import score_answers

def run_gaia_tool_calling_agent(task="gaia", model_id=model_id, action_type="tool_calling"):
    research_agent_answers_file = f"output/{model_id.replace('/', '__')}__{action_type}__{task}.jsonl"
    research_agent = ToolCallAgent(
        model=model,
        tools=[GoogleSearchTool(), VisitWebpageTool(), PythonInterpreterTool(authorized_imports=["numpy", "sympy"]), FinalAnswerTool()],
        max_steps=10
    )
    answer_questions(task, research_agent, action_type, research_agent_answers_file)
    df = score_answers([research_agent_answers_file])
    print(df)

run_gaia_tool_calling_agent()

| Task        | Action Type | Performance      |
|-------------|-----|-----------------|
| SimpleQA       | vanilla  |  |
| SimpleQA       | tool calling  |  |
| MATH       | vanilla  |  |
| MATH       | tool calling  |  |
| GAIA       | vanilla  |  |
| GAIA       | tool calling  |  |